In [10]:
from nytimesarticle import articleAPI
import json
import requests
from bs4 import BeautifulSoup
import pandas as pd
api=articleAPI('QrJWVHaZF2EGlxW6dplgWOTqS4dpD6o1')
import csv

In [11]:
def parse_articles(articles):
    '''
    This function takes in a response to the NYT api and parses
    the articles into a list of dictionaries
    '''
    news = []
    print('hi')
    for i in articles['response']['docs']:
#         print(i)
        dic = {}
#         print(i['type_of_material'])
        dic['id'] = i['_id']
#         if i['abstract'] is not None:
#             dic['abstract'] = i['abstract'].encode("utf8")
        dic['headline'] = i['headline']['main'].encode("utf8")
        dic['desk'] = i['news_desk']
        dic['date'] = i['pub_date'][0:10] # cutting time of day.
        dic['section'] = i['section_name']
        if i['snippet'] is not None:
            dic['snippet'] = i['snippet'].encode("utf8")
        dic['source'] = i['source']
        if i['type_of_material'] is not None:
            dic['type'] = i['type_of_material']
        dic['url'] = i['web_url']
        dic['word_count'] = i['word_count']
        # locations
        locations = []
        for x in range(0,len(i['keywords'])):
            if 'glocations' in i['keywords'][x]['name']:
                locations.append(i['keywords'][x]['value'])
        dic['locations'] = locations
        # subject
        subjects = []
        for x in range(0,len(i['keywords'])):
            if 'subject' in i['keywords'][x]['name']:
                subjects.append(i['keywords'][x]['value'])
        dic['subjects'] = subjects   
        news.append(dic)
    return(news) 

In [12]:
def get_articles(query):
    all_articles = []
    print(query)
    for i in range(0,1): #Range is to specify the pages. Each page has 10 articles so I have used different page numbers to 
        #gather 100 articles on each topic and sub topic. You can see the final csv files of all the topics to clarify the 
        #number of articles collected.
        articles = api.search(q = query,
               begin_date = 20190101,end_date=20190412, page=i)
#         print(articles)
        articles = parse_articles(articles)
        all_articles = all_articles + articles
    return(all_articles)

## Business related articles

In [13]:
business=[]
business_new=get_articles('business')
business=business+business_new

business
hi


In [15]:
business_new[0]
keys = business_new[0].keys()
keys

dict_keys(['id', 'headline', 'desk', 'date', 'section', 'snippet', 'source', 'type', 'url', 'word_count', 'locations', 'subjects'])

#### Don't uncoment and run this as it will save new articles again

In [101]:
# keys = business_new[0].keys()
# with open('bus_1.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(business_new)
# with open('bus_2.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(business_new)
# with open('bus_3.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(business_new)
# with open('bus_4.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(business_new)

In [115]:
# bus_1=pd.read_csv('bus_1.csv')
# bus_2=pd.read_csv('bus_2.csv')
# bus_3=pd.read_csv('bus_3.csv')
# bus_4=pd.read_csv('bus_4.csv')

# df_final=[bus_1,bus_2,bus_3,bus_4]
# df_final=pd.concat(df_final,ignore_index=True,axis=0)
# df_final=df_final.dropna(axis=0)
# df_final.to_csv('final_business.csv',index=False)

In [116]:
df_final=pd.read_csv('final_business.csv')
df_final.shape[0]

150

In [117]:
session = requests.Session()
url=df_final['url'][3]
print(url)
req = session.get(url)
soup = BeautifulSoup(req.text)
print(soup)

https://www.nytimes.com/2019/04/01/business/british-business-brexit.html
<!DOCTYPE html>
<html class="story" itemid="https://www.nytimes.com/2019/04/01/business/british-business-brexit.html" itemscope="true" itemtype="http://schema.org/NewsArticle" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<title data-rh="true">For Many British Businesses, Brexit Has Already Happened - The New York Times</title>
<meta content="en-US" data-rh="true" itemprop="inLanguage"/><meta content="2019-04-01T19:41:13.000Z" data-rh="true" itemprop="datePublished" property="article:published"/><meta content="2019-04-02T13:31:16.772Z" data-rh="true" itemprop="dateModified" property="article:modified"/><meta content="en" data-rh="true" http-equiv="Content-Language"/><meta content="noarchive" data-rh="true" name="robots"/><meta content="100000006435555" data-rh="true" itemprop="identifier" name="articleid"/><meta content="nyt://article/d1aa5a2c-0a5f-5eeb-8bde-996cabceec06" data-rh="true" itempro

In [119]:
article=''
for i in range(1,df_final.shape[0]):
#     print(i)
    session = requests.Session()
    url=df_final['url'][i]
#     print(url)
#     url = "https://www.nytimes.com/2019/03/30/us/politics/mueller-affordable-care-act.html"
    req = session.get(url)
    soup = BeautifulSoup(req.text)
    paragraphs = soup.find_all('div', attrs = {'class': 'css-53u6y8'})
    for i in range(len(paragraphs)):
        article = article + paragraphs[i].get_text()

In [120]:
article

'As an actress, Gwyneth Paltrow was embraced by fans and critics, winning an Oscar for her leading role in “Shakespeare in Love.” As a businesswoman, Ms. Paltrow has received decidedly mixed reviews.Many deride her lifestyle brand, Goop, as little more than an overhyped e-commerce platform peddling pseudoscience and baubles. California regulators secured a $145,000 settlement from Goop last year after suing the company for false advertising, including claims that a $66 vaginal jade egg could balance hormones, increase bladder control and regulate menstrual cycles. Ms. Paltrow is unbowed. Goop is now worth some $250 million, revenues are growing and Ms. Paltrow is looking to Disney for inspiration, visualizing a company that makes money through online retail, offline experiences, ad partnerships and more.Ms. Paltrow grew up around show business. Her father was the producer Bruce Paltrow, who died in 2002, and her mother is the actress Blythe Danner. This pedigree makes it all the harder

In [121]:
with open("data_business.txt", "w", encoding='utf-8') as text_file:
    text_file.write("%s" % article)

## Subtopic- Market related articles

In [126]:
markets=[]
markets_new=get_articles('markets')
markets=markets+markets_new
markets_new[0]

# keys = markets_new[0].keys()
# with open('markets_1.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(markets_new)
# with open('markets_2.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(markets_new)
# with open('markets_3.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(markets_new)
# with open('markets_4.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(markets_new)

# markets_1=pd.read_csv('markets_1.csv')
# markets_2=pd.read_csv('markets_2.csv')
# markets_3=pd.read_csv('markets_3.csv')
# markets_4=pd.read_csv('markets_4.csv')

# df_final=[markets_1,markets_2,markets_3,markets_4]
# df_final=pd.concat(df_final,ignore_index=True,axis=0)
# df_final=df_final.dropna(axis=0)
# df_final.to_csv('final_markets.csv',index=False)

df_final=pd.read_csv('final_markets.csv')
df_final.shape[0]

session = requests.Session()
url=df_final['url'][3]
print(url)
req = session.get(url)
soup = BeautifulSoup(req.text)
print(soup)

article=''
for i in range(1,df_final.shape[0]):
#     print(i)
    session = requests.Session()
    url=df_final['url'][i]
#     print(url)
#     url = "https://www.nytimes.com/2019/03/30/us/politics/mueller-affordable-care-act.html"
    req = session.get(url)
    soup = BeautifulSoup(req.text)
    paragraphs = soup.find_all('div', attrs = {'class': 'css-53u6y8'})
    for i in range(len(paragraphs)):
        article = article + paragraphs[i].get_text()

markets
hi
hi
hi
https://www.nytimes.com/2019/02/28/business/dents-begin-to-show-at-top-end-of-classic-car-market.html
<!DOCTYPE html>
<html class="story" itemid="https://www.nytimes.com/2019/02/28/business/dents-begin-to-show-at-top-end-of-classic-car-market.html" itemscope="true" itemtype="http://schema.org/NewsArticle" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<title data-rh="true">Dents Begin to Show at Top End of Classic Car Market - The New York Times</title>
<meta content="en-US" data-rh="true" itemprop="inLanguage"/><meta content="2019-02-28T12:00:04.000Z" data-rh="true" itemprop="datePublished" property="article:published"/><meta content="2019-03-01T04:40:51.720Z" data-rh="true" itemprop="dateModified" property="article:modified"/><meta content="en" data-rh="true" http-equiv="Content-Language"/><meta content="noarchive" data-rh="true" name="robots"/><meta content="100000006352219" data-rh="true" itemprop="identifier" name="articleid"/><meta content="nyt

In [123]:
article

'WASHINGTON — The number of Americans filing applications for unemployment benefits dropped to a 49-1/2-year low last week, pointing to sustained labor market strength that could assuage fears the economy was rapidly losing momentum.Other data on Thursday showed producer prices increased by the most in five months in March amid a surge in the cost of gasoline. But underlying producer prices remained soft, the latest indication of tame inflation pressures that strengthen the Federal Reserve\'s decision to suspend further interest rate increases this year despite a tight labor market."The economy\'s wheels continue to turn and any thought that growth was going to stop has to be reassessed," said Chris Rupkey, chief economist at MUFG in New York. "Fed officials are on the sidelines awaiting confirmation of what to do next."Initial claims for state unemployment benefits fell 8,000 to a seasonally adjusted 196,000 for the week ended April 6, the Labor Department said. That was the lowest le

In [ ]:
with open("data_markets.txt", "w", encoding='utf-8') as text_file:
    text_file.write("%s" % article)

## Subtopic- Economy related articles

In [128]:
eco=[]
eco_new=get_articles('eco')
eco=eco+eco_new
eco_new[0]

# keys = eco_new[0].keys()
# with open('eco_1.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(eco_new)
# with open('eco_2.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(eco_new)
# with open('eco_3.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(eco_new)
# with open('eco_4.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(eco_new)

# eco_1=pd.read_csv('eco_1.csv')
# eco_2=pd.read_csv('eco_2.csv')
# eco_3=pd.read_csv('eco_3.csv')
# #eco_4=pd.read_csv('eco_4.csv')

# df_final=[eco_1,eco_2,eco_3]
# #,eco_4]
# df_final=pd.concat(df_final,ignore_index=True,axis=0)
# df_final=df_final.dropna(axis=0)
# df_final.to_csv('final_economy.csv',index=False)

df_final=pd.read_csv('final_economy.csv')
df_final.shape[0]

session = requests.Session()
url=df_final['url'][3]
print(url)
req = session.get(url)
soup = BeautifulSoup(req.text)
print(soup)

article=''
for i in range(1,df_final.shape[0]):
#     print(i)
    session = requests.Session()
    url=df_final['url'][i]
    req = session.get(url)
    soup = BeautifulSoup(req.text)
    paragraphs = soup.find_all('div', attrs = {'class': 'css-53u6y8'})
    for i in range(len(paragraphs)):
        article = article + paragraphs[i].get_text()

eco
hi
hi
https://www.nytimes.com/2019/03/28/us/politics/us-economy-trump.html
<!DOCTYPE html>
<html class="story" itemid="https://www.nytimes.com/2019/03/28/us/politics/us-economy-trump.html" itemscope="true" itemtype="http://schema.org/NewsArticle" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<title data-rh="true">Trump Owns the Economy Now, for Better or Worse - The New York Times</title>
<meta content="en-US" data-rh="true" itemprop="inLanguage"/><meta content="2019-03-28T09:00:09.000Z" data-rh="true" itemprop="datePublished" property="article:published"/><meta content="2019-03-29T12:06:38.306Z" data-rh="true" itemprop="dateModified" property="article:modified"/><meta content="en" data-rh="true" http-equiv="Content-Language"/><meta content="noarchive" data-rh="true" name="robots"/><meta content="100000006422346" data-rh="true" itemprop="identifier" name="articleid"/><meta content="nyt://article/c41afc58-a12e-5442-b77b-3a170ee26538" data-rh="true" itemprop="iden

In [129]:
article

'As politicians across the country demand a change in Virginia’s embattled leadership, business leaders are largely sticking to the sidelines.Leading Virginia business groups have stopped short of calling for the resignation of the state’s top three elected officials, all embroiled in personal scandals. Most corporate executives have avoided weighing in at all.And there is no sign that the furor is scaring off investment: Amazon is reportedly wavering in its commitment to open a complex for thousands of workers in New York, where the internet giant has faced opposition, but it has sent no signals about backing out of expansion plans in Northern Virginia.“I’d be very surprised to see business leaders and C.E.O.s weigh in on impeachment proceedings or calls to resign,” said Aaron Chatterji, a Duke University professor who has studied executives’ political interventions. “It’s more seen as an internal Virginia decision.”That reaction stands in contrast to what happened when North Carolina

In [ ]:
with open("data_economy.txt", "w", encoding='utf-8') as text_file:
    text_file.write("%s" % article)

## Subtopic- Money related articles

In [132]:
money=[]
money_new=get_articles('money')
money=money+money_new
money_new[0]

# keys = money_new[0].keys()
# with open('money_1.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(money_new)
# with open('money_2.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(money_new)
# with open('money_3.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(money_new)
# with open('money_4.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(money_new)

# money_1=pd.read_csv('money_1.csv')
# money_2=pd.read_csv('money_2.csv')
# money_3=pd.read_csv('money_3.csv')
# #money_4=pd.read_csv('money_4.csv')

# df_final=[money_1,money_2,money_3]
# #,money_4]
# df_final=pd.concat(df_final,ignore_index=True,axis=0)
# df_final=df_final.dropna(axis=0)
# df_final.to_csv('final_money.csv',index=False)

df_final=pd.read_csv('final_money.csv')
df_final.shape[0]

session = requests.Session()
url=df_final['url'][3]
print(url)
req = session.get(url)
soup = BeautifulSoup(req.text)
print(soup)

article=''
for i in range(1,df_final.shape[0]):
#     print(i)
    session = requests.Session()
    url=df_final['url'][i]
#     print(url)
#     url = "https://www.nytimes.com/2019/03/30/us/politics/mueller-affordable-care-act.html"
    req = session.get(url)
    soup = BeautifulSoup(req.text)
    paragraphs = soup.find_all('div', attrs = {'class': 'css-53u6y8'})
    for i in range(len(paragraphs)):
        article = article + paragraphs[i].get_text()

money
hi
https://www.nytimes.com/reuters/2019/04/12/business/12reuters-space-exploration-virgin-galactic-insight.html
<!DOCTYPE html>
<html class="story" itemid="https://www.nytimes.com/reuters/2019/04/12/business/12reuters-space-exploration-virgin-galactic-insight.html" itemscope="true" itemtype="http://schema.org/NewsArticle" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<title data-rh="true">Cufflinks and the Caribbean: How Virgin Galactic Kept Space Tourists' Interest and Money - The New York Times</title>
<meta content="en-US" data-rh="true" itemprop="inLanguage"/><meta content="2019-04-12T06:46:56.000Z" data-rh="true" itemprop="datePublished" property="article:published"/><meta content="2019-04-12T07:05:28.995Z" data-rh="true" itemprop="dateModified" property="article:modified"/><meta content="en" data-rh="true" http-equiv="Content-Language"/><meta content="noarchive" data-rh="true" name="robots"/><meta content="100000006457740" data-rh="true" itemprop="identi

In [133]:
article

'The Trump International Hotel and Tower in Manhattan, near the southwest corner of Central Park, is a 44-story building with a mix of luxury condominiums and hotel suites that go for more than $2,500 a night.Unit 32G, a two-bedroom, 1,767-square-foot apartment with sweeping views of the park, is owned by an entity called Ecree, which bought the condo in 2014 for $7 million in cash.Documents unearthed by the nonprofit group Global Witness show that the purchase was funded by the daughter of the Republic of Congo’s president, a longtime target of anti-corruption investigators. The funds for the all-cash purchase appear to have been siphoned from that country’s government, according to a report by Global Witness.The purchase took place more than two years before Donald J. Trump became president. Owners of units in the building — 1 Central Park West — pay tens of thousands of dollars a year in condo fees to Mr. Trump’s company, the Trump Organization.A spokeswoman for the Trump Organizati

In [ ]:
with open("data_money.txt", "w", encoding='utf-8') as text_file:
    text_file.write("%s" % article)

## Subtopic- Entrepreneur related articles

In [134]:
entre=[]
entre_new=get_articles('entrepreneur')
entre=entre+entre_new
entre_new[0]

# keys = entre_new[0].keys()
# with open('entre_1.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(entre_new)
# with open('entre_2.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(entre_new)
# with open('entre_3.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(entre_new)
# with open('entre_4.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(entre_new)

# entre_1=pd.read_csv('entre_1.csv')
# entre_2=pd.read_csv('entre_2.csv')
# entre_3=pd.read_csv('entre_3.csv')
# entre_4=pd.read_csv('entre_4.csv')

# df_final=[entre_1,entre_2,entre_3,entre_4]
# df_final=pd.concat(df_final,ignore_index=True,axis=0)
# df_final=df_final.dropna(axis=0)
# df_final.to_csv('final_entre.csv',index=False)

df_final=pd.read_csv('final_entre.csv')
df_final.shape[0]

session = requests.Session()
url=df_final['url'][3]
print(url)
req = session.get(url)
soup = BeautifulSoup(req.text)
print(soup)

article=''
for i in range(1,df_final.shape[0]):
    session = requests.Session()
    url=df_final['url'][i]
    req = session.get(url)
    soup = BeautifulSoup(req.text)
    paragraphs = soup.find_all('div', attrs = {'class': 'css-53u6y8'})
    for i in range(len(paragraphs)):
        article = article + paragraphs[i].get_text()

entrepreneur
hi
https://www.nytimes.com/2019/01/14/us/politics/ivanka-trump-world-bank-president.html
<!DOCTYPE html>
<html class="story" itemid="https://www.nytimes.com/2019/01/14/us/politics/ivanka-trump-world-bank-president.html" itemscope="true" itemtype="http://schema.org/NewsArticle" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<title data-rh="true">Ivanka Trump to Help Choose New World Bank President - The New York Times</title>
<meta content="en-US" data-rh="true" itemprop="inLanguage"/><meta content="2019-01-15T00:40:08.000Z" data-rh="true" itemprop="datePublished" property="article:published"/><meta content="2019-02-05T20:41:41.177Z" data-rh="true" itemprop="dateModified" property="article:modified"/><meta content="en" data-rh="true" http-equiv="Content-Language"/><meta content="noarchive" data-rh="true" name="robots"/><meta content="100000006306138" data-rh="true" itemprop="identifier" name="articleid"/><meta content="nyt://article/89683fee-a9fb-59fd-882

In [135]:
article

'The wealthy of Silicon Valley ought to be living their very best lives right now. John Doerr, an early Amazon and Google investor, calls their moment “the greatest legal accumulation of wealth in history.”And yet, the people of Silicon Valley seem determined to make themselves miserable. They sit in painful, silent meditations for weeks on end. They starve for days — on purpose. Cold morning showers are a bragging right. Notoriety is a badge of honor.So the most helpful clues to understanding Silicon Valley today may come from its favorite ancient philosophy: Stoicism. An ancient Greek school of thought, Stoicism argued that the only real treasures in life were inner virtues, like self-mastery and courage. The Stoics offered tactics to endure pain and pleasure without complaint. These virtues are paraded on the website of a new entrepreneurship-focused lobbying firm, the Cicero Institute. The organization started quietly last year, and is intended to advocate for start-up interests. I

In [ ]:
with open("data_entrepreneur.txt", "w", encoding='utf-8') as text_file:
    text_file.write("%s" % article)

## Subtopic- Energy related articles

In [137]:
energy=[]
energy_new=get_articles('energy')
energy=energy+energy_new
energy_new[0]

# keys = energy_new[0].keys()
# with open('energy_1.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(energy_new)
# with open('energy_2.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(energy_new)
# with open('energy_3.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(energy_new)
# with open('energy_4.csv', 'w', encoding='utf-8', errors='ignore') as output_file:
#     dict_writer = csv.DictWriter(output_file, keys)
#     dict_writer.writeheader()
#     dict_writer.writerows(energy_new)

# energy_1=pd.read_csv('energy_1.csv')
# energy_2=pd.read_csv('energy_2.csv')
# energy_3=pd.read_csv('energy_3.csv')
# energy_4=pd.read_csv('energy_4.csv')
# energy_5=pd.read_csv('energy_5.csv')

# df_final=[energy_1,energy_2,energy_3,energy_4,energy_5]
# df_final=pd.concat(df_final,ignore_index=True,axis=0)
# df_final=df_final.dropna(axis=0)
# df_final.to_csv('final_energy.csv',index=False)

df_final=pd.read_csv('final_energy.csv')
df_final.shape[0]

session = requests.Session()
url=df_final['url'][3]
print(url)
req = session.get(url)
soup = BeautifulSoup(req.text)
print(soup)

article=''
for i in range(1,df_final.shape[0]):
#     print(i)
    session = requests.Session()
    url=df_final['url'][i]
    req = session.get(url)
    soup = BeautifulSoup(req.text)
    paragraphs = soup.find_all('div', attrs = {'class': 'css-53u6y8'})
    for i in range(len(paragraphs)):
        article = article + paragraphs[i].get_text()



energy
hi
https://www.nytimes.com/reuters/2019/04/10/us/politics/10reuters-usa-saudi-nuclearpower.html
<!DOCTYPE html>
<html class="story" itemid="https://www.nytimes.com/reuters/2019/04/10/us/politics/10reuters-usa-saudi-nuclearpower.html" itemscope="true" itemtype="http://schema.org/NewsArticle" lang="en" xmlns:og="http://opengraphprotocol.org/schema/">
<head>
<title data-rh="true">U.S. Senate Bill Mandates Review of Nuclear Power Cooperation With Other Nations - The New York Times</title>
<meta content="en-US" data-rh="true" itemprop="inLanguage"/><meta content="2019-04-10T20:22:19.000Z" data-rh="true" itemprop="datePublished" property="article:published"/><meta content="2019-04-11T00:02:02.115Z" data-rh="true" itemprop="dateModified" property="article:modified"/><meta content="en" data-rh="true" http-equiv="Content-Language"/><meta content="noarchive" data-rh="true" name="robots"/><meta content="100000006454570" data-rh="true" itemprop="identifier" name="articleid"/><meta content="

In [138]:
article

'This article is part of David Leonhardt’s newsletter. You can sign up here to receive it each weekday.The politics of climate change can sometimes feel unwinnable.The oil and coal industries spend large sums of money to spread falsehoods. The leadership of the Republican Party echoes those falsehoods. Many voters, struggling with slow-growing living standards, are hostile to policies that would address climate change — namely, increases in energy prices. And so far the top-tier Democratic presidential candidates haven’t put the issue at the center of their campaigns.But for all of these challenges, I think there is a more promising political approach than many people realize. In the upcoming issue of The Times Magazine, I’ve written an essay about it, and it is online now.The brief version: Americans are skeptical of policies that directly raise the cost of energy, such as a carbon tax or cap-and-trade program. But polls show that most Americans are in favor of policies that promote c

In [ ]:
with open("data_energy.txt", "w", encoding='utf-8') as text_file:
    text_file.write("%s" % article)

## Combining the text files into one text file

In [1]:
import glob

read_files = glob.glob("*.txt")

with open("final_nyt.txt", "w", encoding='utf-8') as outfile:
    for f in read_files:
        with open(f, "r", encoding='utf-8') as infile:
            outfile.write(infile.read())